In [1]:
import os


if "original_dir" in globals():
    # current_dir = os.path.dirname(original_dir)
    current_dir = original_dir
    os.chdir(current_dir)
    print(f"Current directory: {current_dir}")
else:
    original_dir = os.getcwd()
    print(f"Current directory: {original_dir}")

os.chdir("../../../../")
print(f"Changed directory: {os.getcwd()}")

Current directory: d:\northeastern\neu_dev\myo_assist_dev\myosuite\rl_train\myoassist\analyzer
Changed directory: d:\northeastern\neu_dev\myo_assist_dev


In [2]:
import numpy as np
from myosuite.rl_train.myoassist.utils.data_types import DictionableDataclass
from myosuite.rl_train.myoassist.utils.environment_handler import EnvironmentHandler
from myosuite.envs.myoassist import myo_leg_18_imitation
from myosuite.rl_train.myoassist.utils.data_types import DictionableDataclass

MyoSuite:> Registering Myo Envs


In [3]:
config = DictionableDataclass.create(myo_leg_18_imitation.ImitationTrainSessionConfig, None)

In [4]:
config.env_params.env_id = "myoLeg18Imitation-v0"
config.env_params.safe_height = 0.0
config.env_params.out_of_trajectory_threshold = 1000
config.env_params.model_path = "myosuite/simhive/myoassist_sim/gait14dof22musc_cvt3_Right_Toeless_2D.xml"
config.env_params.reference_data_path = "myosuite/simhive/myoassist_sim/reference_motions/neumove_02-constspeed_reduced_humanoid.npz"
config.env_params.num_envs = 1


## If you want lumbar extension

In [5]:
config.env_params.reference_data_keys = ['ankle_angle_l', 'ankle_angle_r',
                                        'hip_flexion_l', 'hip_flexion_r',
                                        'knee_angle_l', 'knee_angle_r',
                                        'pelvis_tilt', 'pelvis_tx', 'pelvis_ty',
                                        'lumbar_extension']
config.env_params.enable_lumbar_joint = True

## No lumbar, no pelvis_tilt; lumbar_rotation following


In [6]:
# config.env_params.reference_data_keys = ['ankle_angle_l', 'ankle_angle_r',
#                                         'hip_flexion_l', 'hip_flexion_r',
#                                         'knee_angle_l', 'knee_angle_r',
#                                         'pelvis_tx', 'pelvis_ty',
#                                         'lumbar_rotation'
#                                         ]
# config.env_params.enable_lumbar_joint = False


## No lumbar, pelvis_tilt following


In [7]:
config.env_params.reference_data_keys = ['ankle_angle_l', 'ankle_angle_r',
                                        'hip_flexion_l', 'hip_flexion_r',
                                        'knee_angle_l', 'knee_angle_r',
                                        'pelvis_tilt', 'pelvis_tx', 'pelvis_ty',
                                        ]
config.env_params.enable_lumbar_joint = False

In [8]:
env = EnvironmentHandler.create_environment(config, False)

Loading reference data from myosuite/simhive/myoassist_sim/reference_motions/neumove_02-constspeed_reduced_humanoid.npz
config.env_params.env_id='myoLeg18Imitation-v0'
=================environment seed: 0=====================
=================environment model_path: myosuite/simhive/myoassist_sim/gait14dof22musc_cvt3_Right_Toeless_2D.xml=====================
    NeuMove MyoLeg18
    
===============================PARAMETERS=============================
self._reward_keys_and_weights=ImitationTrainSessionConfig.EnvParams.RewardWeights(forward_reward=0.01, muscle_activation_penalize=0.1, muscle_activation_diff_penalize=0.1, qpos_imitation_rewards={}, end_effector_imitation_reward=0.3)
===============================PARAMETERS=============================


In [9]:
env.reset()
frames = []
for idx in range(900):
    env.imitation_step(False, idx)

    frame = env.sim.renderer.render_offscreen(camera_id=1,
                                                width=1920,
                                                height=1080)
    frames.append(frame)
env.close()

In [10]:
from IPython.display import HTML
from base64 import b64encode

def show_video_from_frames(frames, video_width=400):
    import skvideo.io
    import tempfile
    import os

    with tempfile.NamedTemporaryFile(delete=False, suffix=".mp4") as temp_video_file:
        temp_video_path = temp_video_file.name

    skvideo.io.vwrite(temp_video_path, np.asarray(frames), outputdict={"-pix_fmt": "yuv420p"})

    with open(temp_video_path, "rb") as video_file:
        video_data = video_file.read()

    os.remove(temp_video_path)

    video_url = f"data:video/mp4;base64,{b64encode(video_data).decode()}"
    return HTML(f"""<video autoplay width={video_width} controls><source src="{video_url}"></video>""")


In [11]:
show_video_from_frames(frames, video_width=1920)